In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
import my_txtutils as txt
from tensorflow.contrib import layers
from tensorflow.contrib import rnn
import os
import time
import math
tf.set_random_seed(0)

/home/ubuntu/anaconda3/lib/python3.6/site-packages/matplotlib/__init__.py:1067: UserWarning: Duplicate key in file "/home/ubuntu/.config/matplotlib/matplotlibrc", line #2
  (fname, cnt))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/matplotlib/__init__.py:1067: UserWarning: Duplicate key in file "/home/ubuntu/.config/matplotlib/matplotlibrc", line #3
  (fname, cnt))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
SEQLEN = 30
BATCHSIZE = 200
ALPHASIZE = txt.ALPHASIZE
INTERNALSIZE = 512
NLAYERS = 3
learning_rate = 0.001
dropout_pkeep = 0.8


In [3]:
shakedir = "shakespeare/*.txt"
codetext, valitext, bookranges = txt.read_data_files(shakedir, validation=True)

Loading file shakespeare/kinghenryviii.txt
Loading file shakespeare/winterstale.txt
Loading file shakespeare/kingrichardiii.txt
Loading file shakespeare/cymbeline.txt
Loading file shakespeare/coriolanus.txt
Loading file shakespeare/merchantofvenice.txt
Loading file shakespeare/comedyoferrors.txt
Loading file shakespeare/2kinghenryvi.txt
Loading file shakespeare/2kinghenryiv.txt
Loading file shakespeare/various.txt
Loading file shakespeare/muchadoaboutnothing.txt
Loading file shakespeare/rapeoflucrece.txt
Loading file shakespeare/twelfthnight.txt
Loading file shakespeare/juliuscaesar.txt
Loading file shakespeare/sonnets.txt
Loading file shakespeare/macbeth.txt
Loading file shakespeare/3kinghenryvi.txt
Loading file shakespeare/tamingoftheshrew.txt
Loading file shakespeare/1kinghenryvi.txt
Loading file shakespeare/antonyandcleopatra.txt
Loading file shakespeare/kinglear.txt
Loading file shakespeare/periclesprinceoftyre.txt
Loading file shakespeare/timonofathens.txt
Loading file shakespear

In [4]:
epoch_size = len(codetext) // (BATCHSIZE * SEQLEN)
txt.print_data_stats(len(codetext), len(valitext), epoch_size)


Training text size is 4.91MB with 128.49KB set aside for validation. There will be 858 batches per epoch


In [5]:
lr = tf.placeholder(tf.float32, name='lr')
pkeep = tf.placeholder(tf.float32, name ='pkeep')
batchsize = tf.placeholder(tf.int32, name='batchsize')

In [6]:
X = tf.placeholder(tf.uint8, [None,None], name ='X')
Xo = tf.one_hot(X, ALPHASIZE, 1.0, 0.0)

Y_ = tf.placeholder(tf.uint8, [None,None], name='Y_')
Yo_ = tf.one_hot(Y_, ALPHASIZE, 1.0, 0.0)

Hin = tf.placeholder(tf.float32, [None, INTERNALSIZE*NLAYERS], name='Hin')


In [7]:
cells = [rnn.GRUCell(INTERNALSIZE) for _ in range(NLAYERS)]

In [8]:
dropcells = [rnn.DropoutWrapper(cell,input_keep_prob=pkeep) for cell in cells]
multicell = rnn.MultiRNNCell(dropcells, state_is_tuple=False)
multicell = rnn.DropoutWrapper(multicell, output_keep_prob=pkeep)

In [9]:
zerostate = multicell.zero_state(BATCHSIZE, dtype=tf.float32)
Yr, H = tf.nn.dynamic_rnn(multicell, Xo, dtype=tf.float32, initial_state=Hin)

In [10]:
H = tf.identity(H, name='H')

In [11]:
Yflat = tf.reshape(Yr, [-1, INTERNALSIZE])
Ylogits = layers.linear(Yflat, ALPHASIZE)
Yflat_ = tf.reshape(Yo_, [-1, ALPHASIZE])
loss = tf.nn.softmax_cross_entropy_with_logits(logits=Ylogits, labels=Yflat_)
loss = tf.reshape(loss, [batchsize, -1])
Yo = tf.nn.softmax(Ylogits, name ='Yo')
Y = tf.argmax(Yo, 1)
Y = tf.reshape(Y,[batchsize, -1], name="Y")

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See @{tf.nn.softmax_cross_entropy_with_logits_v2}.



In [12]:
train_step = tf.train.AdamOptimizer(lr).minimize(loss)

In [13]:
seqloss =tf.reduce_mean(loss, 1)
batchloss = tf.reduce_mean(seqloss)
accuracy = tf.reduce_mean(tf.cast(tf.equal(Y_, tf.cast(Y, tf.uint8)), tf.float32))
loss_summary = tf.summary.scalar("batch_loss" , batchloss)
acc_summary = tf.summary.scalar("batch_accuracy" , accuracy)
summaries = tf.summary.merge([loss_summary, acc_summary])

In [22]:
timestamp = str(math.trunc(time.time()))
summary_writer = tf.summary.FileWriter("log/" + timestamp + "-training")
validation_writer = tf.summary.FileWriter("log/" +timestamp + "-validation")

In [15]:
if not os.path.exists("checkpoints"):
    os.mkdir("checkpoints")
saver = tf.train.Saver(max_to_keep=1)

In [16]:
DISPLAY_FREQ = 50
_50_BATCHES = DISPLAY_FREQ * BATCHSIZE * SEQLEN
progress = txt.Progress(DISPLAY_FREQ, size=111+2, msg="Training on next "+str(DISPLAY_FREQ)+" batches")


In [17]:

istate = np.zeros([BATCHSIZE, INTERNALSIZE*NLAYERS])
init = tf.global_variables_initializer()
sess = tf.Session()
sess.run(init)
step =0

In [23]:
for x, y_, epoch in txt.rnn_minibatch_sequencer(codetext, BATCHSIZE, SEQLEN, nb_epochs=10):
    
    feed_dict = {X: x, Y_: y_, Hin: istate, lr: learning_rate, pkeep: dropout_pkeep, batchsize: BATCHSIZE }
    _, y, ostate = sess.run([train_step, Y, H], feed_dict = feed_dict)
    
    if step % _50_BATCHES == 0:
        feed_dict = {X: x, Y_: y_, Hin: istate, pkeep: 1.0, batchsize: BATCHSIZE}  # no dropout for validation
        y, l, bl, acc, smm = sess.run([Y, seqloss, batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_learning_learned_comparison(x, y, l, bookranges, bl, acc, epoch_size, step, epoch)
        summary_writer.add_summary(smm, step)
        
    if step % _50_BATCHES == 0 and len(valitext) > 0:
        VALI_SEQLEN = 1*1024  # Sequence length for validation. State will be wrong at the start of each sequence.
        bsize = len(valitext) // VALI_SEQLEN
        txt.print_validation_header(len(codetext), bookranges)
        vali_x, vali_y, _ = next(txt.rnn_minibatch_sequencer(valitext, bsize, VALI_SEQLEN, 1))  # all data in 1 batch
        vali_nullstate = np.zeros([bsize, INTERNALSIZE*NLAYERS])
        feed_dict = {X: vali_x, Y_: vali_y, Hin: vali_nullstate, pkeep: 1.0,  # no dropout for validation
                     batchsize: bsize}
        ls, acc, smm = sess.run([batchloss, accuracy, summaries], feed_dict=feed_dict)
        txt.print_validation_stats(ls, acc)
        # save validation data for Tensorboard
        validation_writer.add_summary(smm, step)
        
    if step // 3 % _50_BATCHES == 0:
        txt.print_text_generation_header()
        ry = np.array([[txt.convert_from_alphabet(ord("K"))]])
        rh = np.zeros([1, INTERNALSIZE * NLAYERS])
        for k in range(1000):
            ryo, rh = sess.run([Yo, H], feed_dict={X: ry, pkeep: 1.0, Hin: rh, batchsize: 1})
            rc = txt.sample_from_probabilities(ryo, topn=10 if epoch <= 1 else 2)
            print(chr(txt.convert_to_alphabet(rc)), end="")
            ry = np.array([[rc]])
        txt.print_text_generation_footer()
    
    
    if step // 10 % _50_BATCHES == 0:
        saved_file = saver.save(sess, 'checkpoints/rnn_train_' + timestamp, global_step=step)
        print("Saved file: " + saved_file)
        
        
    progress.step(reset=step % _50_BATCHES == 0)
    
    istate = ostate
    step += BATCHSIZE * SEQLEN
    
        
        
        
        
        

    
    


   0 (epoch 0) kinghenryviii.txt │  KING HENRY VIII\\\ DRAMATIS P │ ho   IhRIE I \\\\\\I EIINI  I  │ loss: 2.92294
  30 (epoch 0) kinghenryviii.txt │ s but merely\ A fit or two o'  │ eter te e e  Tndothtn thertrdh │ loss: 2.50080
  60 (epoch 0) kinghenryviii.txt │ :\ I will have none so near el │   I totl tote tord tortorr tre │ loss: 2.09645
  90 (epoch 0) kinghenryviii.txt │ d perish.\\CARDINAL WOLSEY If  │  toren  \\ ARIEN   IhRII  I  t │ loss: 2.50159
 120 (epoch 0) kinghenryviii.txt │ , accompanied with other\ Lear │  tneoreendn  toth tn er  Tort  │ loss: 2.40979
 150 (epoch 0) kinghenryviii.txt │ attend with patience.\\ [Enter │    r  toth torhnn o \\ [Enter  │ loss: 1.87310
 180 (epoch 0) kinghenryviii.txt │  thanks. How say you?\ My pris │ ooer   \Ior tot tour\ Io toane │ loss: 2.42887
 210 (epoch 0) kinghenryviii.txt │ rry; now\ I trust I shall. My  │ e   aor  T thel  t toetl \Io t │ loss: 2.39502
 240 (epoch 0) kinghenryviii.txt │ \ Camillo for the minister to  │  Iotene nto

VALIDATION STATS:                                  loss: 2.39815,       accuracy: 0.33324

┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
trree mals tirt ands in brant sens hothacs wowen

	O ELENLA	I o hat hrt soth no tre crole bentare these
	A mem mang irtonerdint tieg on felrste oud sorrsots tharlangs menteneet
	Tom soor hin ald.
TLONCUE	C E teet I work the sothire,
	Arlt berares te certrele int hou bales
	Ancerath snleed whes holese oratt.
	Anthere,'a on af in tomes bire foor ferlo tort
	I wor tinthoreror aresestish tose seses.

	And tir wrytt thausd foutsorr houl ores.

TATENO	Eudr ben tarlone thold is the soore.

Thor indere my of andorer
	Suntse sornes,
	Tithe pamtronsoten atsenthe manterat hert weas tonreassonr thaels.
	Thatten we hering teimes
	Inces wete the cingettite bele thl oramorer fers that wicl weart al ang ofrentee foron.,
	[Rulrin Ir onme as and tht wore batill;
	Wh the srand wigs. Themst amleth asdirs

VALIDATION STATS:                                  loss: 2.28115,       accuracy: 0.35180

0%                                        Training on next 50 batches                                        100%
600000 (epoch 0) cymbeline.txt │  man may weep upon his wedding │ wandtan ti r tn n tis wire ng  │ loss: 2.28701
600030 (epoch 0) cymbeline.txt │ lse; which I would not be,\ Fo │ o   aiesh t wi ld tot te   Tor │ loss: 1.74031
600060 (epoch 0) cymbeline.txt │ ere?\\ [Enter Chamberlain]\\Ch │    \\ [Exter tAeneen  nn \\ Ae │ loss: 1.94535
600090 (epoch 0) cymbeline.txt │ angely.\\SURREY O, how, how?\\ │ n     \\CAREAN I  aeu  to   \  │ loss: 2.33377
600120 (epoch 0) cymbeline.txt │ t be wedged in more: I am stif │  te tir    tn tere \a wn toene │ loss: 2.18597
600150 (epoch 0) cymbeline.txt │ o little study, that my teachi │ ttosh e to r   ahet se shere n │ loss: 2.22645
600180 (epoch 0) cymbeline.txt │ e paddling palms and pinching  │  trre eng torl  tnd trrge ng t │ loss: 2.24791
6002

VALIDATION STATS:                                  loss: 2.18626,       accuracy: 0.36948

0%                                        Training on next 50 batches                                        100%
900000 (epoch 0) merchantofvenice.txt │ ol and beggar. The two kings,\ │ d tnd te een  Ihe wheuteng     │ loss: 2.01695
900030 (epoch 0) merchantofvenice.txt │ omen placed together makes col │  e  trone  ah h  er tane  aoml │ loss: 2.21846
900060 (epoch 0) merchantofvenice.txt │  [Exit Chamberlain]\\ANNE My h │ [Exen]MEeneen enn]\\ RTONIe la │ loss: 2.08379
900090 (epoch 0) merchantofvenice.txt │ posted, as the agent of our ca │ art r  an the wne   tf tfr ton │ loss: 1.76399
900120 (epoch 0) merchantofvenice.txt │ of a queen;\ As holy oil, Edwa │ f tnduenn   Tn teul tfrl an en │ loss: 2.52257
900150 (epoch 0) merchantofvenice.txt │ bt, as you do conscience\ In d │ th an tou ta tondeenn e  T  to │ loss: 1.90736
900180 (epoch 0) merchantofvenice.txt │ ction of my brains\ And harden │ e 

VALIDATION STATS:                                  loss: 2.11100,       accuracy: 0.38914

┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
ayt full to ane ane fore,
	In watttino ald so mall and sisteck.

MARLOTIUS	That ip thay theye bir of ast in and oth thouet
	Tat thou thy fave hes a will and shath beall. ' woll nour to tho by to beint,'thaks
	oweld on tret wn hat this day.

LICIND	Nonken tho kie, an yat miser hords, beacl trut s ighoo then that I ting
	stor have to ting hand ast weese hestedis nas.

HINONANDORI	I dey my hore.

BIMON	Whim boot de wame, the south noved ate hut tis an my.-	All net fase as they fech of sould hail to foms
	And to they lind wath sham an shus hand.
	Hat seall he aran hy fall hamp beated it tham
	I wlat well tay huntlad tat is of, whend I a per then lage.
	Hat be les, fy shead anfratlt
	to but will bears wowh mesolloss of my lore?
	Ihet sall me hit bluch tho thou when him thik sore;
	If thay 

...

VALIDATION STATS:                                  loss: 1.43031,       accuracy: 0.57233

0%                                        Training on next 50 batches                                        100%
50400000 (epoch 9) 1kinghenryiv.txt │  To what we wildly do, so we p │ Th saot te sall y so  Io melwr │ loss: 1.64320
50400030 (epoch 9) 1kinghenryiv.txt │  your father:\ Your honour not │ tou  hather,\ Iou  honour sot  │ loss: 0.82205
50400060 (epoch 9) 1kinghenryiv.txt │ arence,\ With lies well steel' │ rence.\ Ahth hofs ai l ceaad d │ loss: 1.19731
50400090 (epoch 9) 1kinghenryiv.txt │  To serve me well, you all sho │ Ah teeve ye till, Iou mrl thau │ loss: 1.26038
50400120 (epoch 9) 1kinghenryiv.txt │ evenge it; whom I will importu │ senge tt  ahi  I sill nnport\n │ loss: 1.10515
50400150 (epoch 9) 1kinghenryiv.txt │ a twelve-month hence,\ That th │ nshonve -areh oarce.\ That Ihe │ loss: 1.43955
50400180 (epoch 9) 1kinghenryiv.txt │ e child, Your brother's son;\  │  soaldr aor  lro

VALIDATION STATS:                                  loss: 1.43434,       accuracy: 0.57160

┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
e and seem to the court.

ARCHBISHOP OF YORK	What, with a life of many man and heart
	To see them with the state of men and means,
	The storms of many and the strong and story
	Which, when his son was seen the woman of the world
	That shall be seen and be a soul to make
	The state and the gods, whose love and her soul
	Shall be to break out off a part of them.
	The gods, we will beseech your grace to be a word.
	The more that was not worth the season to my loving store.

BUCKINGHAM	Well, we were seen, my lord, what shall I say
	To see you with the state, that would not have
	Before yet we must be a man as shall
	I should not love you to the word.

BIRON	Well means, I would not have my love and mean.

KING HENRY VI	I will be sad that words me will not be.

KING HENRY VI	I am not so, I 

VALIDATION STATS:                                  loss: 1.42599,       accuracy: 0.57510

0%                                        Training on next 50 batches                                        100%
51000000 (epoch 9) romeoandjuliet.txt │  fasting: they throng who\ sho │ toitiog  aher aheowg tiem shou │ loss: 1.55512
51000030 (epoch 9) romeoandjuliet.txt │ n worries he his\ daughter wit │ stiudebs tirwas  peughter aith │ loss: 1.39529
51000060 (epoch 9) romeoandjuliet.txt │ ,\ His soul thou canst not hav │ \ Aas sonl thau sanst not save │ loss: 0.81302
51000090 (epoch 9) romeoandjuliet.txt │ to fatting for his pains\ God  │ h tilheng oor tis srrns, Ao  b │ loss: 1.49517
51000120 (epoch 9) romeoandjuliet.txt │ they are gone.\\QUEEN ELIZABET │ her sre none.\\ UEEN ELIZABETH │ loss: 0.46259
51000150 (epoch 9) romeoandjuliet.txt │  of came into my mind.\ What,  │ of houe an o ty sand,\\What  w │ loss: 1.18362
51000180 (epoch 9) romeoandjuliet.txt │ BETH The king! why, who's that │ ET

VALIDATION STATS:                                  loss: 1.41601,       accuracy: 0.57751
Saved file: checkpoints/rnn_train_1528466181-51000000

0%                                        Training on next 50 batches                                        100%
51300000 (epoch 9) kinghenryv.txt │ t, man; here's no harm intende │   tyd  ae e s ao monm on onded │ loss: 1.29010
51300030 (epoch 9) kinghenryv.txt │ h, was when, at the relation o │   ahs tean  ts the sesition of │ loss: 1.32361
51300060 (epoch 9) kinghenryv.txt │ n,\ For these known evils, but │    Tor the e tiows pyels  aut  │ loss: 1.30447
51300090 (epoch 9) kinghenryv.txt │ \ When you have done, repair t │  [har tou have sone  aepeir to │ loss: 0.95252
51300120 (epoch 9) kinghenryv.txt │  mind,\ Love, charity, obedien │ hand.\ Teoe  aoargty, arsyienc │ loss: 1.28571
51300150 (epoch 9) kinghenryv.txt │ spilt.\\RATCLIFF Make haste; t │ oerl,\  ITCLIFF Iyre minte  ah │ loss: 1.42564
51300180 (epoch 9) kinghenryv.txt │ fe, nor E

VALIDATION STATS:                                  loss: 1.42521,       accuracy: 0.57562

┌───────────────────────────────────Generating random text from learned state───────────────────────────────────┐
ing, and the great gentleman
That she should be a secret solemn shall be worth
The sea that shall be with him, that he should be so desired,
To see his woman have so sooths that he hath seen him.
The season was the strength of his sheet proceeding,
Which he hath seen the world,
And so she show'd the heart of heaven, that have he stay'd
That thou shouldst see, as thou shalt see his sound and stands,
That thou shouldst see him to the greatest strong of this shame,
To the good words of the seas stands of heart,
To take her stranger shame the stronger shame on his desire.

'This is thy short, thou shaktst, and shall be so did see thee strike,
And then thou shouldst, thou shalt not stay the state,
And so to thee thy soul as thou shalt be,
That thou shalt be the service that I shall be so.
